<a href="https://colab.research.google.com/github/ceying/DataSparsityProject_CreditStability/blob/main/HomeCreditStability_RunBest_March2025.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Setup

In [ ]:
!pip install optuna

In [ ]:
import optuna

In [ ]:
pip install category_encoders

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.7/85.7 kB 5.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.5/13.5 MB 95.8 MB/s eta 0:00:00
  Attempting uninstall: scikit-learn
    Found existing installation: scikit-learn 1.3.1
    Uninstalling scikit-learn-1.3.1:
      Successfully uninstalled scikit-learn-1.3.1


In [ ]:
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.preprocessing import OneHotEncoder, StandardScaler, LabelEncoder, StandardScaler
from sklearn.model_selection import train_test_split, GridSearchCV, KFold, cross_val_score, RandomizedSearchCV
from sklearn.model_selection import StratifiedKFold
from statsmodels.stats.outliers_influence import variance_inflation_factor
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import OrdinalEncoder
#from category_encoders import HashingEncoder

#from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
#from sklearn.ensemble import VotingClassifier
from sklearn.ensemble import RandomForestClassifier
#from sklearn.ensemble import AdaBoostClassifier
#from sklearn.ensemble import GradientBoostingClassifier
from xgboost import XGBClassifier
import xgboost as xgb
import lightgbm as lgb
#from catboost import CatBoostClassifier

from sklearn import metrics
from sklearn.metrics import f1_score, precision_score, recall_score, roc_auc_score, accuracy_score, balanced_accuracy_score


from sklearn.calibration import calibration_curve
from sklearn.tree import plot_tree

np.random.seed(0)

In [ ]:
from sklearn.experimental import enable_iterative_imputer  # noqa
from sklearn.impute import IterativeImputer

In [ ]:
# display all outputs
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [ ]:
from google.colab import drive

drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
def calculate_metrics(y_val, y_pred_proba):
    # Convert predicted probabilities to class labels (0 and 1)
    y_pred_class = (y_pred_proba >= 0.5).astype(int)

    # Calculate the metrics
    metrics = {
        'Metric': ['F1 Score', 'Precision', 'Recall', 'ROC AUC', 'Accuracy', 'Balanced Accuracy'],
        'Value': [f1_score(y_val, y_pred_class),
                   precision_score(y_val, y_pred_class, zero_division=0),
                   recall_score(y_val, y_pred_class),
                   roc_auc_score(y_val, y_pred_proba),
                   accuracy_score(y_val, y_pred_class),
                   balanced_accuracy_score(y_val, y_pred_class)]
    }

    # Create a DataFrame
    df = pd.DataFrame(metrics)

    return df

In [ ]:
def combine_metrics(df_low, df_mid, df_high, calculate_metrics):
    """
    Combines metrics for different completeness levels into a single DataFrame.

    Args:
    - df_low (pd.DataFrame): DataFrame for low completeness level.
    - df_mid (pd.DataFrame): DataFrame for mid completeness level.
    - df_high (pd.DataFrame): DataFrame for high completeness level.
    - calculate_metrics (function): Function to calculate metrics.

    Returns:
    - pd.DataFrame: Combined metrics DataFrame.
    """
    # Calculate metrics for each completeness level
    metrics_low = calculate_metrics(df_low['y_test'], df_low['y_pred_proba'])
    metrics_mid = calculate_metrics(df_mid['y_test'], df_mid['y_pred_proba'])
    metrics_high = calculate_metrics(df_high['y_test'], df_high['y_pred_proba'])


    # Merge metrics DataFrames
    combined_metrics = metrics_low.merge(metrics_mid, on='Metric', suffixes=('_low', '_mid'))
    combined_metrics = combined_metrics.merge(metrics_high, on='Metric', suffixes=('', '_high'))
    combined_metrics = combined_metrics.rename(columns={'Value': 'Value_high'})

    # Clean up combined metrics DataFrame
    combined_metrics = combined_metrics.drop(columns=[col for col in combined_metrics.columns if 'completeness_level' in col])
    combined_metrics = combined_metrics.set_index('Metric')

    return combined_metrics

#Load Data

In [ ]:
df_raw = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/df_train.csv')
df_raw.head()

<ipython-input-97-229bff99e930>:1: DtypeWarning: Columns (256,257,258,259,260,261,272,289,294,296,297,298,299,300,301,302,303,304,305,306,307,308,309,310,311,312,313,314,315,316,317,326,327,328,329,336,339,340,341,344,345) have mixed types. Specify dtype option on import or set low_memory=False.
  df_raw = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/df_train.csv')


case_id  WEEK_NUM  target  month_decision  weekday_decision  \
0        0         0       0               1                 4   
1        1         0       0               1                 4   
2        2         0       0               1                 5   
3        3         0       0               1                 4   
4        4         0       1               1                 5   

   credamount_770A  applicationcnt_361L  applications30d_658L  \
0          30000.0                  0.0                   0.0   
1          19999.8                  0.0                   0.0   
2          78000.0                  0.0                   0.0   
3          40000.0                  0.0                   1.0   
4          44000.0                  0.0                   1.0   

   applicationscnt_1086L  applicationscnt_464L  ...  max_sex_738L  \
0                    0.0                   0.0  ...             F   
1                    0.0                   0.0  ...             M   
2                    0.0                   0.0  ...             F   
3                    0.0                   2.0  ...             F   
4                    0.0                   0.0  ...             F   

     max_type_25L  last_contaddr_matchlist_1032L  \
0  PRIMARY_MOBILE                            NaN   
1  PRIMARY_MOBILE                            NaN   
2  PRIMARY_MOBILE                            NaN   
3  PRIMARY_MOBILE                            NaN   
4  PRIMARY_MOBILE                            NaN   

   last_contaddr_smempladdr_334L  last_incometype_1044T  \
0                            NaN                    NaN   
1                            NaN                    NaN   
2                            NaN                    NaN   
3                            NaN                    NaN   
4                            NaN                    NaN   

   last_relationshiptoclient_642T  last_role_1084L  \
0                       COLLEAGUE               PE   
1                  OTHER_RELATIVE               PE   
2                          SPOUSE               PE   
3                          SPOUSE               PE   
4                         SIBLING               PE   

   last_safeguarantyflag_411L  last_sex_738L  last_type_25L  
0                         NaN            NaN          PHONE  
1                         NaN            NaN          PHONE  
2                         NaN            NaN          PHONE  
3                         NaN            NaN          PHONE  
4                         NaN            NaN          PHONE  

[5 rows x 347 columns]

In [ ]:
df = df_raw.copy()

In [ ]:
df.info(verbose=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1526659 entries, 0 to 1526658
Data columns (total 347 columns):
 #    Column                                Dtype  
---   ------                                -----  
 0    case_id                               int64  
 1    WEEK_NUM                              int64  
 2    target                                int64  
 3    month_decision                        int64  
 4    weekday_decision                      int64  
 5    credamount_770A                       float64
 6    applicationcnt_361L                   float64
 7    applications30d_658L                  float64
 8    applicationscnt_1086L                 float64
 9    applicationscnt_464L                  float64
 10   applicationscnt_867L                  float64
 11   clientscnt_1022L                      float64
 12   clientscnt_100L                       float64
 13   clientscnt_1071L                      float64
 14   clientscnt_1130L                      float64
 1

## Completeness level

In [ ]:
df['completeness'] = (1 - df.isnull().sum(axis=1) / len(df.columns)) * 100


In [ ]:
# prompt: create a new categorical column for completeness level: low for completeness < 40, mid for completeness between 40 and 80, high for completeness over 80

# Create the new categorical column 'completeness_level'
df['completeness_level'] = pd.cut(df['completeness'], bins=[0, 40, 80, 100], labels=['low', 'mid', 'high'], right=False)

# Display the first few rows to verify the new column
print(df[['completeness', 'completeness_level']].head())


   completeness completeness_level
0     27.953890                low
1     27.953890                low
2     42.939481                mid
3     43.227666                mid
4     41.498559                mid


In [ ]:
# prompt: group by completeness level, show count of target = 0,   target  = 1, and % of target = 1

# Assuming 'df' is already defined and contains 'target' and 'completeness_level' columns
completeness_summary = df.groupby('completeness_level')['target'].agg(['value_counts'])
completeness_summary = completeness_summary.unstack()
completeness_summary.columns = completeness_summary.columns.droplevel(0)
completeness_summary['%_target_0'] = (completeness_summary[0] / (completeness_summary[0] + completeness_summary[1])) * 100
completeness_summary['%_target_1'] = (completeness_summary[1] / (completeness_summary[0] + completeness_summary[1])) * 100
completeness_summary


<ipython-input-11-b5a660268458>:4: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  completeness_summary = df.groupby('completeness_level')['target'].agg(['value_counts'])


target                   0      1  %_target_0  %_target_1
completeness_level                                       
low                  77074   2083   97.368521    2.631479
mid                 536990  16746   96.975815    3.024185
high                864601  29165   96.736842    3.263158

## Downsampling majority class

In [ ]:
from sklearn.utils import resample


# Group data by 'completeness_level'
grouped = df.groupby('completeness_level')

# Initialize an empty list to store the downsampled DataFrames
downsampled_dfs = []

# Iterate over each group
for name, group in grouped:
    # Separate target variable
    majority_class = group['target'].value_counts().index[0]
    minority_class = group['target'].value_counts().index[1]
    majority_df = group[group['target'] == majority_class]
    minority_df = group[group['target'] == minority_class]

    # Downsample the majority class within the current group
    downsampled_majority_df = resample(majority_df,
                                          replace=False,
                                          n_samples=len(minority_df),
                                          random_state=42)
    # Combine the downsampled majority class with the minority class
    balanced_group = pd.concat([downsampled_majority_df, minority_df])

    downsampled_dfs.append(balanced_group)

# Concatenate all the downsampled groups back into a single DataFrame
full_balanced_df = pd.concat(downsampled_dfs)




<ipython-input-129-27f150ad6bb3>:5: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  grouped = df.groupby('completeness_level')


In [ ]:
full_balanced_df['target'].value_counts()
full_balanced_df['completeness_level'].value_counts()

target
0    47994
1    47994
Name: count, dtype: int64

completeness_level
high    58330
mid     33492
low      4166
Name: count, dtype: int64

In [ ]:
full_balanced_df.to_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/full_balanced_df.csv', index=False)


In [ ]:
full_balanced_df = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/full_balanced_df.csv')

<ipython-input-98-f6eb06f8cafc>:1: DtypeWarning: Columns (261,272,289,294,326,327) have mixed types. Specify dtype option on import or set low_memory=False.
  full_balanced_df = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/full_balanced_df.csv')


In [ ]:
X = full_balanced_df.drop(columns=["target", "case_id", "WEEK_NUM","completeness"], axis=1)
y = full_balanced_df['target']


In [ ]:
y.value_counts()

target
0    47994
1    47994
Name: count, dtype: int64

In [ ]:
X['completeness_level'].value_counts()

completeness_level
high    58330
mid     33492
low      4166
Name: count, dtype: int64

## Preprocessing

In [ ]:
#++++++++++++++++++++++++++++++++++++++++++++++++++++
## NEW ##
#++++++++++++++++++++++++++++++++++++++++++++++++++++
from sklearn.base import BaseEstimator, TransformerMixin
from category_encoders import TargetEncoder

# Define preprocessing steps for numerical and categorical variables
numerical_features = X.select_dtypes(include=['int64', 'float64']).columns
categorical_features = X.select_dtypes(include=['object']).columns
date_features = X.select_dtypes(include=['datetime64[ns]']).columns

# Create a pipeline for categorical features with imputation and encoding
categorical_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='constant', fill_value='missing')),
    ('target', TargetEncoder())
])

# Create a pipeline for numerical features with imputation
class MissingIndicatorTransformer(BaseEstimator, TransformerMixin):
    def fit(self, X, y=None):
        return self

    def transform(self, X, y=None):
        missing_indicator = X.isnull().astype(int)
        return pd.concat([X, missing_indicator], axis=1)

numerical_transformer = Pipeline(steps=[
    ('missing_indicator', MissingIndicatorTransformer())
])

# Define the ColumnTransformer to apply transformations to different feature types
preprocessor = ColumnTransformer(
    transformers=[
        ('num', numerical_transformer, numerical_features),
        ('cat', categorical_transformer, categorical_features)
    ]
)

In [ ]:
# Fit the preprocessor to the entire training dataset
preprocessor.fit(X, y)

# Transform the training and validation datasets
X_preprocessed = preprocessor.transform(X)

ColumnTransformer(transformers=[('num',
                                 Pipeline(steps=[('missing_indicator',
                                                  MissingIndicatorTransformer())]),
                                 Index(['month_decision', 'weekday_decision', 'credamount_770A',
       'applicationcnt_361L', 'applications30d_658L', 'applicationscnt_1086L',
       'applicationscnt_464L', 'applicationscnt_867L', 'clientscnt_1022L',
       'clientscnt_100L',
       ...
       'max_numberofoutstandinst...
       'max_incometype_1044T', 'max_relationshiptoclient_415T',
       'max_relationshiptoclient_642T', 'max_remitter_829L', 'max_role_1084L',
       'max_safeguarantyflag_411L', 'max_sex_738L', 'max_type_25L',
       'last_contaddr_matchlist_1032L', 'last_contaddr_smempladdr_334L',
       'last_incometype_1044T', 'last_relationshiptoclient_642T',
       'last_role_1084L', 'last_safeguarantyflag_411L', 'last_sex_738L',
       'last_type_25L'],
      dtype='object'))])

/usr/local/lib/python3.11/dist-packages/sklearn/pipeline.py:62: FutureWarning: This Pipeline instance is not fitted yet. Call 'fit' with appropriate arguments before using other methods such as transform, predict, etc. This will raise an error in 1.8 instead of the current warning.
  warnings.warn(


In [ ]:
X_preprocessed

array([[3.00000000e+00, 4.00000000e+00, 4.79378000e+04, ...,
        5.15971494e-01, 5.15971494e-01, 5.24211483e-01],
       [7.00000000e+00, 3.00000000e+00, 1.79740000e+04, ...,
        4.97187365e-01, 4.49022155e-01, 4.85678993e-01],
       [2.00000000e+00, 2.00000000e+00, 8.45760000e+04, ...,
        5.15971494e-01, 5.15971494e-01, 5.24211483e-01],
       ...,
       [1.00000000e+01, 6.00000000e+00, 6.18140000e+04, ...,
        4.83564296e-01, 4.49022155e-01, 4.85678993e-01],
       [1.00000000e+01, 1.00000000e+00, 1.20000000e+05, ...,
        4.83564296e-01, 4.49022155e-01, 4.85678993e-01],
       [1.00000000e+01, 1.00000000e+00, 2.00000000e+05, ...,
        4.83564296e-01, 4.49022155e-01, 4.85678993e-01]])

In [ ]:
X_preprocessed.to_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Full_balanced_df_X_preprocessed.csv', index=False)

#Model Setup

In [ ]:
X_preprocessed = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Full_balanced_df_X_preprocessed.csv')

In [ ]:
full_balanced_df = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/full_balanced_df.csv')

<ipython-input-12-f6eb06f8cafc>:1: DtypeWarning: Columns (261,272,289,294,326,327) have mixed types. Specify dtype option on import or set low_memory=False.
  full_balanced_df = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/full_balanced_df.csv')


In [ ]:
X = full_balanced_df.drop(columns=["target", "case_id", "WEEK_NUM","completeness"], axis=1)
y = full_balanced_df['target']


In [ ]:
y.value_counts()

target
0    47994
1    47994
Name: count, dtype: int64

In [ ]:
X['completeness_level'].value_counts()

completeness_level
high    58330
mid     33492
low      4166
Name: count, dtype: int64

In [ ]:
import pandas as pd
from sklearn.model_selection import train_test_split

def split_data(X, X_preprocessed, y, test_size=0.2, num_splits=50):
    """
    Splits the preprocessed data into training and testing sets.

    Args:
    - X (pd.DataFrame): Original feature data with index.
    - X_preprocessed (array-like): Preprocessed feature data.
    - y (pd.Series): Target variable.
    - test_size (float, optional): Proportion of data for testing. Defaults to 0.2.
    - num_splits (int, optional): Number of splits to generate. Defaults to 5.

    Returns:
    - A list of tuples, where each tuple contains X_train, X_test, y_train, y_test, train_index, and test_index for a given split.
    """
    splits = []
    for i in range(num_splits):
        # Split data with varying random state
        X_train, X_test, y_train, y_test = train_test_split(X_preprocessed, y, test_size=test_size, random_state=i)

        # Split data with fixed random state to get indices
        X_preprocessed_indexed = pd.DataFrame(X_preprocessed, index=X.index)
        X_train_indexed, X_test_indexed, y_train_indexed, y_test_indexed = train_test_split(X_preprocessed_indexed, y, test_size=test_size, random_state=i)
        train_index = X_train_indexed.index
        test_index = X_test_indexed.index

        splits.append((X_train, X_test, y_train, y_test, train_index, test_index))

    return splits

In [ ]:
splits = split_data(X, X_preprocessed, y)


## Decision Tree

In [ ]:
import joblib
study = joblib.load('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/optuna_DT_study.pkl')


In [ ]:
best_params = study.best_params
best_model = DecisionTreeClassifier(random_state=42)
best_model.set_params(**{k: v for k, v in best_params.items() if k != 'model'})

DecisionTreeClassifier(max_depth=7, min_samples_leaf=3, min_samples_split=9,
                       random_state=42)

In [ ]:
# prompt: create a new dataframe with y_test, y_pred_probas and test_index for each iteration

# Initialize an empty list to store DataFrames for each iteration
all_results = []

for i, (X_train, X_test, y_train, y_test, train_index, test_index) in enumerate(splits):
    print(f"Iteration {i+1}:")

    # Retrain the best model
    best_model.fit(X_train, y_train)

    # Predict probabilities using the best model
    y_pred_proba = best_model.predict_proba(X_test)[:, 1]

    # Create a DataFrame for the current iteration
    iteration_results = pd.DataFrame({
        'y_test': y_test,
        'y_pred_proba': y_pred_proba,
        'test_index': test_index,
        'iteration': i
    })

    all_results.append(iteration_results)


Iteration 1:


DecisionTreeClassifier(max_depth=7, min_samples_leaf=3, min_samples_split=9,
                       random_state=42)

Iteration 2:


DecisionTreeClassifier(max_depth=7, min_samples_leaf=3, min_samples_split=9,
                       random_state=42)

Iteration 3:


...

DecisionTreeClassifier(max_depth=7, min_samples_leaf=3, min_samples_split=9,
                       random_state=42)

Iteration 49:


DecisionTreeClassifier(max_depth=7, min_samples_leaf=3, min_samples_split=9,
                       random_state=42)

Iteration 50:


DecisionTreeClassifier(max_depth=7, min_samples_leaf=3, min_samples_split=9,
                       random_state=42)

In [ ]:
# Concatenate all iteration results into a single DataFrame
final_results_df = pd.concat(all_results, ignore_index=True)
final_results_df

y_test  y_pred_proba  test_index  iteration
0            1      0.731983       24203          0
1            1      0.775148       77881          0
2            0      0.113986       50081          0
3            0      0.113986       52555          0
4            1      0.690063       91382          0
...        ...           ...         ...        ...
959895       1      0.900789       78211         49
959896       0      0.148430       58097         49
959897       0      0.640376          79         49
959898       0      0.082632       54335         49
959899       0      0.177750       48447         49

[959900 rows x 4 columns]

In [ ]:
final_results_df = pd.merge(final_results_df, full_balanced_df[['completeness', 'completeness_level']], left_on='test_index', right_index=True, how='left')
final_results_df

y_test  y_pred_proba  test_index  iteration  completeness  \
0            1      0.731983       24203          0     62.247839   
1            1      0.775148       77881          0     80.691643   
2            0      0.113986       50081          0     90.201729   
3            0      0.113986       52555          0     88.472622   
4            1      0.690063       91382          0     80.115274   
...        ...           ...         ...        ...           ...   
959895       1      0.900789       78211         49     85.302594   
959896       0      0.148430       58097         49     89.625360   
959897       0      0.640376          79         49     27.089337   
959898       0      0.082632       54335         49     89.913545   
959899       0      0.177750       48447         49     88.184438   

       completeness_level  
0                     mid  
1                    high  
2                    high  
3                    high  
4                    high  
...                   ...  
959895               high  
959896               high  
959897                low  
959898               high  
959899               high  

[959900 rows x 6 columns]

In [ ]:
final_results_df.to_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new50_DT_final_results_df.csv', index=False)

In [ ]:
for iteration in final_results_df['iteration'].unique():
    # Create sub_df for the current iteration
    sub_df = final_results_df[final_results_df['iteration'] == iteration]

    # Define df_low, df_mid, and df_high based on 'completeness_level'
    df_low = sub_df[sub_df['completeness_level'] == 'low']
    df_mid = sub_df[sub_df['completeness_level'] == 'mid']
    df_high = sub_df[sub_df['completeness_level'] == 'high']

    # Check if all completeness levels exist in the sub_df
    if not (df_low.empty or df_mid.empty or df_high.empty):
        # Run combine_metrics for the current iteration
        combined_metrics_result = combine_metrics(df_low, df_mid, df_high, calculate_metrics)
        print(f"Combined Metrics for Iteration {iteration}:\n{combined_metrics_result}")
    else:
        print(f"Skipping Iteration {iteration}: Not all completeness levels present.")


Combined Metrics for Iteration 0:
                   Value_low  Value_mid  Value_high
Metric                                             
F1 Score            0.631229   0.674294    0.695968
Precision           0.580448   0.651371    0.674571
Recall              0.691748   0.698889    0.718766
ROC AUC             0.636415   0.731677    0.759342
Accuracy            0.604982   0.665974    0.689898
Balanced Accuracy   0.606895   0.666317    0.690252
Combined Metrics for Iteration 1:
                   Value_low  Value_mid  Value_high
Metric                                             
F1 Score            0.611180   0.693818    0.701129
Precision           0.643979   0.666015    0.690982
Recall              0.581560   0.724044    0.711578
ROC AUC             0.657661   0.747875    0.759890
Accuracy            0.633060   0.687082    0.696936
Balanced Accuracy   0.632641   0.687830    0.696948
Combined Metrics for Iteration 2:
                   Value_low  Value_mid  Value_high
Metric        

In [ ]:
# Initialize an empty list to store combined metrics results
combined_metrics_results = []

for iteration in final_results_df['iteration'].unique():
    # Create sub_df for the current iteration
    sub_df = final_results_df[final_results_df['iteration'] == iteration]

    # Define df_low, df_mid, and df_high based on 'completeness_level'
    df_low = sub_df[sub_df['completeness_level'] == 'low']
    df_mid = sub_df[sub_df['completeness_level'] == 'mid']
    df_high = sub_df[sub_df['completeness_level'] == 'high']

    # Check if all completeness levels exist in the sub_df
    if not (df_low.empty or df_mid.empty or df_high.empty):
        # Run combine_metrics for the current iteration
        combined_metrics_result = combine_metrics(df_low, df_mid, df_high, calculate_metrics)
        combined_metrics_result['iteration'] = iteration

        # Append the result to the list
        combined_metrics_results.append(combined_metrics_result)
    else:
        print(f"Skipping Iteration {iteration}: Not all completeness levels present.")



In [ ]:
combined_metrics_result

Value_low  Value_mid  Value_high  iteration
Metric                                                        
F1 Score            0.626480   0.704433    0.706503         49
Precision           0.596311   0.664973    0.668356         49
Recall              0.659864   0.748871    0.749268         49
ROC AUC             0.602116   0.737153    0.753936         49
Accuracy            0.606129   0.687434    0.689433         49
Balanced Accuracy   0.606068   0.687755    0.689566         49

In [ ]:
# Concatenate the list of DataFrames into a single DataFrame
combined_metrics_df = pd.concat(combined_metrics_results, ignore_index=False)

# Set the index to include the iteration number
combined_metrics_df = combined_metrics_df.reset_index().set_index(['iteration', 'Metric'])

In [ ]:
combined_metrics_df

Value_low  Value_mid  Value_high
iteration Metric                                             
0         F1 Score            0.631229   0.674294    0.695968
          Precision           0.580448   0.651371    0.674571
          Recall              0.691748   0.698889    0.718766
          ROC AUC             0.636415   0.731677    0.759342
          Accuracy            0.604982   0.665974    0.689898
...                                ...        ...         ...
49        Precision           0.596311   0.664973    0.668356
          Recall              0.659864   0.748871    0.749268
          ROC AUC             0.602116   0.737153    0.753936
          Accuracy            0.606129   0.687434    0.689433
          Balanced Accuracy   0.606068   0.687755    0.689566

[300 rows x 3 columns]

In [ ]:
combined_metrics_df.to_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new50_DT_combined_metrics_df.csv')

## Random Forest

In [ ]:
best_params = {'max_depth':24, 'min_samples_split':32, 'n_estimators':237}
best_model = RandomForestClassifier(random_state=42)
best_model.set_params(**{k: v for k, v in best_params.items() if k != 'model'})

RandomForestClassifier(max_depth=24, min_samples_split=32, n_estimators=237,
                       random_state=42)

In [ ]:
# prompt: create a new dataframe with y_test, y_pred_probas and test_index for each iteration

# Initialize an empty list to store DataFrames for each iteration
all_results = []

for i, (X_train, X_test, y_train, y_test, train_index, test_index) in enumerate(splits):
    print(f"Iteration {i+1}:")

    # Retrain the best model
    best_model.fit(X_train, y_train)

    # Predict probabilities using the best model
    y_pred_proba = best_model.predict_proba(X_test)[:, 1]

    # Create a DataFrame for the current iteration
    iteration_results = pd.DataFrame({
        'y_test': y_test,
        'y_pred_proba': y_pred_proba,
        'test_index': test_index,
        'iteration': i
    })

    all_results.append(iteration_results)


Iteration 1:


RandomForestClassifier(max_depth=24, min_samples_split=32, n_estimators=237,
                       random_state=42)

Iteration 2:


RandomForestClassifier(max_depth=24, min_samples_split=32, n_estimators=237,
                       random_state=42)

Iteration 3:


...

RandomForestClassifier(max_depth=24, min_samples_split=32, n_estimators=237,
                       random_state=42)

Iteration 49:


RandomForestClassifier(max_depth=24, min_samples_split=32, n_estimators=237,
                       random_state=42)

Iteration 50:


RandomForestClassifier(max_depth=24, min_samples_split=32, n_estimators=237,
                       random_state=42)

In [ ]:
# Concatenate all iteration results into a single DataFrame
final_results_df = pd.concat(all_results, ignore_index=True)
final_results_df

y_test  y_pred_proba  test_index  iteration
0            1      0.749422       24203          0
1            1      0.645641       77881          0
2            0      0.172363       50081          0
3            0      0.172207       52555          0
4            1      0.585506       91382          0
...        ...           ...         ...        ...
959895       1      0.905110       78211         49
959896       0      0.062379       58097         49
959897       0      0.455657          79         49
959898       0      0.049435       54335         49
959899       0      0.238794       48447         49

[959900 rows x 4 columns]

In [ ]:
final_results_df = pd.merge(final_results_df, full_balanced_df[['completeness', 'completeness_level']], left_on='test_index', right_index=True, how='left')
final_results_df

y_test  y_pred_proba  test_index  iteration  completeness  \
0            1      0.749422       24203          0     62.247839   
1            1      0.645641       77881          0     80.691643   
2            0      0.172363       50081          0     90.201729   
3            0      0.172207       52555          0     88.472622   
4            1      0.585506       91382          0     80.115274   
...        ...           ...         ...        ...           ...   
959895       1      0.905110       78211         49     85.302594   
959896       0      0.062379       58097         49     89.625360   
959897       0      0.455657          79         49     27.089337   
959898       0      0.049435       54335         49     89.913545   
959899       0      0.238794       48447         49     88.184438   

       completeness_level  
0                     mid  
1                    high  
2                    high  
3                    high  
4                    high  
...                   ...  
959895               high  
959896               high  
959897                low  
959898               high  
959899               high  

[959900 rows x 6 columns]

In [ ]:
final_results_df.to_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new50_RF_final_results_df.csv', index=False)

In [ ]:
for iteration in final_results_df['iteration'].unique():
    # Create sub_df for the current iteration
    sub_df = final_results_df[final_results_df['iteration'] == iteration]

    # Define df_low, df_mid, and df_high based on 'completeness_level'
    df_low = sub_df[sub_df['completeness_level'] == 'low']
    df_mid = sub_df[sub_df['completeness_level'] == 'mid']
    df_high = sub_df[sub_df['completeness_level'] == 'high']

    # Check if all completeness levels exist in the sub_df
    if not (df_low.empty or df_mid.empty or df_high.empty):
        # Run combine_metrics for the current iteration
        combined_metrics_result = combine_metrics(df_low, df_mid, df_high, calculate_metrics)
        print(f"Combined Metrics for Iteration {iteration}:\n{combined_metrics_result}")
    else:
        print(f"Skipping Iteration {iteration}: Not all completeness levels present.")


Combined Metrics for Iteration 0:
                   Value_low  Value_mid  Value_high
Metric                                             
F1 Score            0.697941   0.748341    0.760784
Precision           0.660173   0.720478    0.729907
Recall              0.740291   0.778445    0.794389
ROC AUC             0.748125   0.814221    0.828256
Accuracy            0.686833   0.740977    0.753313
Balanced Accuracy   0.688011   0.741368    0.753815
Combined Metrics for Iteration 1:
                   Value_low  Value_mid  Value_high
Metric                                             
F1 Score            0.705882   0.756677    0.761802
Precision           0.665272   0.732386    0.735870
Recall              0.751773   0.782635    0.789628
ROC AUC             0.764325   0.827405    0.829310
Accuracy            0.689332   0.753531    0.753314
Balanced Accuracy   0.689840   0.754120    0.753345
Combined Metrics for Iteration 2:
                   Value_low  Value_mid  Value_high
Metric        

In [ ]:
# Initialize an empty list to store combined metrics results
combined_metrics_results = []

for iteration in final_results_df['iteration'].unique():
    # Create sub_df for the current iteration
    sub_df = final_results_df[final_results_df['iteration'] == iteration]

    # Define df_low, df_mid, and df_high based on 'completeness_level'
    df_low = sub_df[sub_df['completeness_level'] == 'low']
    df_mid = sub_df[sub_df['completeness_level'] == 'mid']
    df_high = sub_df[sub_df['completeness_level'] == 'high']

    # Check if all completeness levels exist in the sub_df
    if not (df_low.empty or df_mid.empty or df_high.empty):
        # Run combine_metrics for the current iteration
        combined_metrics_result = combine_metrics(df_low, df_mid, df_high, calculate_metrics)
        combined_metrics_result['iteration'] = iteration

        # Append the result to the list
        combined_metrics_results.append(combined_metrics_result)
    else:
        print(f"Skipping Iteration {iteration}: Not all completeness levels present.")



In [ ]:
combined_metrics_result

Value_low  Value_mid  Value_high  iteration
Metric                                                        
F1 Score            0.698031   0.750655    0.758848         49
Precision           0.674419   0.726147    0.728381         49
Recall              0.723356   0.776874    0.791975         49
ROC AUC             0.746954   0.813424    0.823085         49
Accuracy            0.686720   0.743298    0.748883         49
Balanced Accuracy   0.686678   0.743473    0.748979         49

In [ ]:
# Concatenate the list of DataFrames into a single DataFrame
combined_metrics_df = pd.concat(combined_metrics_results, ignore_index=False)

# Set the index to include the iteration number
combined_metrics_df = combined_metrics_df.reset_index().set_index(['iteration', 'Metric'])

In [ ]:
combined_metrics_df

Value_low  Value_mid  Value_high
iteration Metric                                             
0         F1 Score            0.697941   0.748341    0.760784
          Precision           0.660173   0.720478    0.729907
          Recall              0.740291   0.778445    0.794389
          ROC AUC             0.748125   0.814221    0.828256
          Accuracy            0.686833   0.740977    0.753313
...                                ...        ...         ...
49        Precision           0.674419   0.726147    0.728381
          Recall              0.723356   0.776874    0.791975
          ROC AUC             0.746954   0.813424    0.823085
          Accuracy            0.686720   0.743298    0.748883
          Balanced Accuracy   0.686678   0.743473    0.748979

[300 rows x 3 columns]

In [ ]:
combined_metrics_df.to_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new50_RF_combined_metrics_df.csv')

## LGBM

In [ ]:
best_params = {'bagging_fraction':0.6010244841816326, 'bagging_freq':1,
               'colsample_bytree':0.6528309604226257,
               'learning_rate':0.020268448211189685, 'max_depth':8,
               'min_data_in_leaf':77, 'min_sum_hessian_in_leaf':0.21888724252263048,
               'n_estimators':448, 'num_leaves':646, 'random_state':42,
               'reg_alpha':6.120851143796912e-07, 'reg_lambda':0.8997170865092138,
               'subsample':0.8827014036642549}

In [ ]:
best_model = lgb.LGBMClassifier(random_state=42)
best_model.set_params(**{k: v for k, v in best_params.items() if k != 'model'})

LGBMClassifier(bagging_fraction=0.6010244841816326, bagging_freq=1,
               colsample_bytree=0.6528309604226257,
               learning_rate=0.020268448211189685, max_depth=8,
               min_data_in_leaf=77, min_sum_hessian_in_leaf=0.21888724252263048,
               n_estimators=448, num_leaves=646, random_state=42,
               reg_alpha=6.120851143796912e-07, reg_lambda=0.8997170865092138,
               subsample=0.8827014036642549)

In [ ]:
# prompt: create a new dataframe with y_test, y_pred_probas and test_index for each iteration

# Initialize an empty list to store DataFrames for each iteration
all_results = []

for i, (X_train, X_test, y_train, y_test, train_index, test_index) in enumerate(splits):
    print(f"Iteration {i+1}:")

    # Retrain the best model
    best_model.fit(X_train, y_train)

    # Predict probabilities using the best model
    y_pred_proba = best_model.predict_proba(X_test)[:, 1]

    # Create a DataFrame for the current iteration
    iteration_results = pd.DataFrame({
        'y_test': y_test,
        'y_pred_proba': y_pred_proba,
        'test_index': test_index,
        'iteration': i
    })

    all_results.append(iteration_results)


Iteration 1:
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=0.21888724252263048, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=0.21888724252263048
[LightGBM] [Warning] min_data_in_leaf is set=77, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=77
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] bagging_fraction is set=0.6010244841816326, subsample=0.8827014036642549 will be ignored. Current value: bagging_fraction=0.6010244841816326
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=0.21888724252263048, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=0.21888724252263048
[LightGBM] [Warning] min_data_in_leaf is set=77, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=77
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] 

LGBMClassifier(bagging_fraction=0.6010244841816326, bagging_freq=1,
               colsample_bytree=0.6528309604226257,
               learning_rate=0.020268448211189685, max_depth=8,
               min_data_in_leaf=77, min_sum_hessian_in_leaf=0.21888724252263048,
               n_estimators=448, num_leaves=646, random_state=42,
               reg_alpha=6.120851143796912e-07, reg_lambda=0.8997170865092138,
               subsample=0.8827014036642549)

[LightGBM] [Warning] min_sum_hessian_in_leaf is set=0.21888724252263048, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=0.21888724252263048
[LightGBM] [Warning] min_data_in_leaf is set=77, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=77
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] bagging_fraction is set=0.6010244841816326, subsample=0.8827014036642549 will be ignored. Current value: bagging_fraction=0.6010244841816326
Iteration 2:
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=0.21888724252263048, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=0.21888724252263048
[LightGBM] [Warning] min_data_in_leaf is set=77, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=77
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] 

LGBMClassifier(bagging_fraction=0.6010244841816326, bagging_freq=1,
               colsample_bytree=0.6528309604226257,
               learning_rate=0.020268448211189685, max_depth=8,
               min_data_in_leaf=77, min_sum_hessian_in_leaf=0.21888724252263048,
               n_estimators=448, num_leaves=646, random_state=42,
               reg_alpha=6.120851143796912e-07, reg_lambda=0.8997170865092138,
               subsample=0.8827014036642549)

[LightGBM] [Warning] min_sum_hessian_in_leaf is set=0.21888724252263048, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=0.21888724252263048
[LightGBM] [Warning] min_data_in_leaf is set=77, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=77
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] bagging_fraction is set=0.6010244841816326, subsample=0.8827014036642549 will be ignored. Current value: bagging_fraction=0.6010244841816326
Iteration 3:
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=0.21888724252263048, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=0.21888724252263048
[LightGBM] [Warning] min_data_in_leaf is set=77, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=77
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] 

...

[LightGBM] [Warning] min_sum_hessian_in_leaf is set=0.21888724252263048, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=0.21888724252263048
[LightGBM] [Warning] min_data_in_leaf is set=77, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=77
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] bagging_fraction is set=0.6010244841816326, subsample=0.8827014036642549 will be ignored. Current value: bagging_fraction=0.6010244841816326
Iteration 49:
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=0.21888724252263048, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=0.21888724252263048
[LightGBM] [Warning] min_data_in_leaf is set=77, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=77
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning]

LGBMClassifier(bagging_fraction=0.6010244841816326, bagging_freq=1,
               colsample_bytree=0.6528309604226257,
               learning_rate=0.020268448211189685, max_depth=8,
               min_data_in_leaf=77, min_sum_hessian_in_leaf=0.21888724252263048,
               n_estimators=448, num_leaves=646, random_state=42,
               reg_alpha=6.120851143796912e-07, reg_lambda=0.8997170865092138,
               subsample=0.8827014036642549)

[LightGBM] [Warning] min_sum_hessian_in_leaf is set=0.21888724252263048, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=0.21888724252263048
[LightGBM] [Warning] min_data_in_leaf is set=77, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=77
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] bagging_fraction is set=0.6010244841816326, subsample=0.8827014036642549 will be ignored. Current value: bagging_fraction=0.6010244841816326
Iteration 50:
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=0.21888724252263048, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=0.21888724252263048
[LightGBM] [Warning] min_data_in_leaf is set=77, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=77
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning]

LGBMClassifier(bagging_fraction=0.6010244841816326, bagging_freq=1,
               colsample_bytree=0.6528309604226257,
               learning_rate=0.020268448211189685, max_depth=8,
               min_data_in_leaf=77, min_sum_hessian_in_leaf=0.21888724252263048,
               n_estimators=448, num_leaves=646, random_state=42,
               reg_alpha=6.120851143796912e-07, reg_lambda=0.8997170865092138,
               subsample=0.8827014036642549)

[LightGBM] [Warning] min_sum_hessian_in_leaf is set=0.21888724252263048, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=0.21888724252263048
[LightGBM] [Warning] min_data_in_leaf is set=77, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=77
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] bagging_fraction is set=0.6010244841816326, subsample=0.8827014036642549 will be ignored. Current value: bagging_fraction=0.6010244841816326


In [ ]:
# Concatenate all iteration results into a single DataFrame
final_results_df = pd.concat(all_results, ignore_index=True)
final_results_df

y_test  y_pred_proba  test_index  iteration
0            1      0.863152       24203          0
1            1      0.804602       77881          0
2            0      0.046961       50081          0
3            0      0.116721       52555          0
4            1      0.688801       91382          0
...        ...           ...         ...        ...
959895       1      0.933936       78211         49
959896       0      0.039504       58097         49
959897       0      0.430316          79         49
959898       0      0.035136       54335         49
959899       0      0.084400       48447         49

[959900 rows x 4 columns]

In [ ]:
final_results_df = pd.merge(final_results_df, full_balanced_df[['completeness', 'completeness_level']], left_on='test_index', right_index=True, how='left')
final_results_df

y_test  y_pred_proba  test_index  iteration  completeness  \
0            1      0.863152       24203          0     62.247839   
1            1      0.804602       77881          0     80.691643   
2            0      0.046961       50081          0     90.201729   
3            0      0.116721       52555          0     88.472622   
4            1      0.688801       91382          0     80.115274   
...        ...           ...         ...        ...           ...   
959895       1      0.933936       78211         49     85.302594   
959896       0      0.039504       58097         49     89.625360   
959897       0      0.430316          79         49     27.089337   
959898       0      0.035136       54335         49     89.913545   
959899       0      0.084400       48447         49     88.184438   

       completeness_level  
0                     mid  
1                    high  
2                    high  
3                    high  
4                    high  
...                   ...  
959895               high  
959896               high  
959897                low  
959898               high  
959899               high  

[959900 rows x 6 columns]

In [ ]:
final_results_df.to_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new50_LGBM_final_results_df.csv', index=False)

In [ ]:
for iteration in final_results_df['iteration'].unique():
    # Create sub_df for the current iteration
    sub_df = final_results_df[final_results_df['iteration'] == iteration]

    # Define df_low, df_mid, and df_high based on 'completeness_level'
    df_low = sub_df[sub_df['completeness_level'] == 'low']
    df_mid = sub_df[sub_df['completeness_level'] == 'mid']
    df_high = sub_df[sub_df['completeness_level'] == 'high']

    # Check if all completeness levels exist in the sub_df
    if not (df_low.empty or df_mid.empty or df_high.empty):
        # Run combine_metrics for the current iteration
        combined_metrics_result = combine_metrics(df_low, df_mid, df_high, calculate_metrics)
        print(f"Combined Metrics for Iteration {iteration}:\n{combined_metrics_result}")
    else:
        print(f"Skipping Iteration {iteration}: Not all completeness levels present.")


Combined Metrics for Iteration 0:
                   Value_low  Value_mid  Value_high
Metric                                             
F1 Score            0.703271   0.766472    0.784619
Precision           0.677928   0.744970    0.755566
Recall              0.730583   0.789252    0.815996
ROC AUC             0.765335   0.838059    0.859357
Accuracy            0.698695   0.762067    0.778782
Balanced Accuracy   0.699398   0.762351    0.779237
Combined Metrics for Iteration 1:
                   Value_low  Value_mid  Value_high
Metric                                             
F1 Score            0.703371   0.772318    0.781198
Precision           0.670236   0.751364    0.759103
Recall              0.739953   0.794475    0.804618
ROC AUC             0.761774   0.849125    0.856415
Accuracy            0.690504   0.770626    0.774832
Balanced Accuracy   0.690907   0.771109    0.774858
Combined Metrics for Iteration 2:
                   Value_low  Value_mid  Value_high
Metric        

In [ ]:
# Initialize an empty list to store combined metrics results
combined_metrics_results = []

for iteration in final_results_df['iteration'].unique():
    # Create sub_df for the current iteration
    sub_df = final_results_df[final_results_df['iteration'] == iteration]

    # Define df_low, df_mid, and df_high based on 'completeness_level'
    df_low = sub_df[sub_df['completeness_level'] == 'low']
    df_mid = sub_df[sub_df['completeness_level'] == 'mid']
    df_high = sub_df[sub_df['completeness_level'] == 'high']

    # Check if all completeness levels exist in the sub_df
    if not (df_low.empty or df_mid.empty or df_high.empty):
        # Run combine_metrics for the current iteration
        combined_metrics_result = combine_metrics(df_low, df_mid, df_high, calculate_metrics)
        combined_metrics_result['iteration'] = iteration

        # Append the result to the list
        combined_metrics_results.append(combined_metrics_result)
    else:
        print(f"Skipping Iteration {iteration}: Not all completeness levels present.")



In [ ]:
combined_metrics_result

Value_low  Value_mid  Value_high  iteration
Metric                                                        
F1 Score            0.701987   0.768736    0.785625         49
Precision           0.683871   0.746595    0.761558         49
Recall              0.721088   0.792231    0.811262         49
ROC AUC             0.755143   0.839118    0.854424         49
Accuracy            0.693530   0.762917    0.779124         49
Balanced Accuracy   0.693499   0.763070    0.779195         49

In [ ]:
# Concatenate the list of DataFrames into a single DataFrame
combined_metrics_df = pd.concat(combined_metrics_results, ignore_index=False)

# Set the index to include the iteration number
combined_metrics_df = combined_metrics_df.reset_index().set_index(['iteration', 'Metric'])

In [ ]:
combined_metrics_df

Value_low  Value_mid  Value_high
iteration Metric                                             
0         F1 Score            0.703271   0.766472    0.784619
          Precision           0.677928   0.744970    0.755566
          Recall              0.730583   0.789252    0.815996
          ROC AUC             0.765335   0.838059    0.859357
          Accuracy            0.698695   0.762067    0.778782
...                                ...        ...         ...
49        Precision           0.683871   0.746595    0.761558
          Recall              0.721088   0.792231    0.811262
          ROC AUC             0.755143   0.839118    0.854424
          Accuracy            0.693530   0.762917    0.779124
          Balanced Accuracy   0.693499   0.763070    0.779195

[300 rows x 3 columns]

In [ ]:
combined_metrics_df.to_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new50_LGBM_combined_metrics_df.csv')

## XGB


In [ ]:
!pip uninstall -y scikit-learn
!pip install scikit-learn==1.3.1

Found existing installation: scikit-learn 1.6.1
Uninstalling scikit-learn-1.6.1:
  Successfully uninstalled scikit-learn-1.6.1
  Using cached scikit_learn-1.3.1-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (11 kB)
Using cached scikit_learn-1.3.1-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (10.9 MB)
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
category-encoders 2.8.0 requires scikit-learn>=1.6.0, but you have scikit-learn 1.3.1 which is incompatible.
imbalanced-learn 0.13.0 requires scikit-learn<2,>=1.3.2, but you have scikit-learn 1.3.1 which is incompatible.


In [ ]:
import sklearn
import xgboost

print(f"scikit-learn version: {sklearn.__version__}")
print(f"xgboost version: {xgboost.__version__}")

scikit-learn version: 1.3.1
xgboost version: 2.1.4


In [ ]:
import joblib
import xgboost as xgb

# Load the study object
study = joblib.load('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/optuna_XGB_study.pkl')

# Access the best hyperparameters
best_params = study.best_params

# Initialize and set up the XGBoost classifier with the best parameters
best_model = xgb.XGBClassifier(random_state=42, **best_params)

In [ ]:
import pandas as pd

X_preprocessed = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Full_balanced_df_X_preprocessed.csv')
X_preprocessed


0    1            2    3    4    5    6     7    8    9  ...  \
0       3.0  4.0   47937.8000  0.0  0.0  0.0  0.0   0.0  0.0  0.0  ...   
1       7.0  3.0   17974.0000  0.0  0.0  0.0  0.0   0.0  0.0  0.0  ...   
2       2.0  2.0   84576.0000  0.0  0.0  0.0  2.0   0.0  0.0  0.0  ...   
3       5.0  6.0    7749.8003  0.0  0.0  0.0  0.0   1.0  1.0  0.0  ...   
4       4.0  1.0   23372.0000  0.0  0.0  0.0  0.0   0.0  0.0  0.0  ...   
...     ...  ...          ...  ...  ...  ...  ...   ...  ...  ...  ...   
95983  10.0  5.0   61814.0000  0.0  0.0  0.0  0.0   2.0  0.0  0.0  ...   
95984  10.0  5.0  100000.0000  0.0  0.0  0.0  0.0  12.0  0.0  0.0  ...   
95985  10.0  6.0   61814.0000  0.0  0.0  0.0  0.0   2.0  0.0  0.0  ...   
95986  10.0  1.0  120000.0000  0.0  0.0  0.0  0.0   0.0  0.0  0.0  ...   
95987  10.0  1.0  200000.0000  0.0  0.0  0.0  0.0   9.0  0.0  0.0  ...   

            587       588       589       590       591       592       593  \
0      0.455431  0.500021  0.515971  0.515971  0.515971  0.570655  0.525107   
1      0.455431  0.500021  0.484216  0.484226  0.463334  0.483362  0.481169   
2      0.455431  0.500021  0.515971  0.515971  0.515971  0.462197  0.525107   
3      0.455431  0.500021  0.515971  0.515971  0.515971  0.403364  0.525107   
4      0.560738  0.500021  0.515971  0.515971  0.515971  0.570655  0.525107   
...         ...       ...       ...       ...       ...       ...       ...   
95983  0.455431  0.500021  0.484216  0.484226  0.463334  0.483362  0.481169   
95984  0.560738  0.500021  0.484216  0.484226  0.525685  0.483362  0.481169   
95985  0.455431  0.500021  0.484216  0.484226  0.463334  0.483362  0.481169   
95986  0.455431  0.500021  0.484216  0.484226  0.525685  0.483362  0.481169   
95987  0.455431  0.500021  0.484216  0.484226  0.463334  0.483362  0.481169   

            594       595       596  
0      0.515971  0.515971  0.524211  
1      0.497187  0.449022  0.485679  
2      0.515971  0.515971  0.524211  
3      0.515971  0.515971  0.524211  
4      0.515971  0.515971  0.524211  
...         ...       ...       ...  
95983  0.497187  0.449022  0.485679  
95984  0.497187  0.538308  0.485679  
95985  0.483564  0.449022  0.485679  
95986  0.483564  0.449022  0.485679  
95987  0.483564  0.449022  0.485679  

[95988 rows x 597 columns]

In [ ]:
full_balanced_df = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/full_balanced_df.csv')

<ipython-input-4-f6eb06f8cafc>:1: DtypeWarning: Columns (261,272,289,294,326,327) have mixed types. Specify dtype option on import or set low_memory=False.
  full_balanced_df = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/full_balanced_df.csv')


In [ ]:
X = full_balanced_df.drop(columns=["target", "case_id", "WEEK_NUM","completeness"], axis=1)
y = full_balanced_df['target']


In [ ]:
splits = split_data(X, X_preprocessed, y)

In [ ]:
# prompt: create a new dataframe with y_test, y_pred_probas and test_index for each iteration

# Initialize an empty list to store DataFrames for each iteration
all_results = []

for i, (X_train, X_test, y_train, y_test, train_index, test_index) in enumerate(splits):
    print(f"Iteration {i+1}:")

    # Retrain the best model
    best_model.fit(X_train, y_train)

    # Predict probabilities using the best model
    y_pred_proba = best_model.predict_proba(X_test)[:, 1]

    # Create a DataFrame for the current iteration
    iteration_results = pd.DataFrame({
        'y_test': y_test,
        'y_pred_proba': y_pred_proba,
        'test_index': test_index,
        'iteration': i
    })

    all_results.append(iteration_results)


Iteration 1:
Iteration 2:
Iteration 3:
Iteration 4:
Iteration 5:
Iteration 6:
Iteration 7:
Iteration 8:
Iteration 9:
Iteration 10:
Iteration 11:
Iteration 12:
Iteration 13:
Iteration 14:
Iteration 15:
Iteration 16:
Iteration 17:
Iteration 18:
Iteration 19:
Iteration 20:
Iteration 21:
Iteration 22:
Iteration 23:
Iteration 24:
Iteration 25:
Iteration 26:
Iteration 27:
Iteration 28:
Iteration 29:
Iteration 30:
Iteration 31:
Iteration 32:
Iteration 33:
Iteration 34:
Iteration 35:
Iteration 36:
Iteration 37:
Iteration 38:
Iteration 39:
Iteration 40:
Iteration 41:
Iteration 42:
Iteration 43:
Iteration 44:
Iteration 45:
Iteration 46:
Iteration 47:
Iteration 48:
Iteration 49:
Iteration 50:


In [ ]:
# Concatenate all iteration results into a single DataFrame
final_results_df = pd.concat(all_results, ignore_index=True)
final_results_df

y_test  y_pred_proba  test_index  iteration
0            1      0.960844       24203          0
1            1      0.689335       77881          0
2            0      0.027819       50081          0
3            0      0.163814       52555          0
4            1      0.841738       91382          0
...        ...           ...         ...        ...
959895       1      0.967337       78211         49
959896       0      0.032402       58097         49
959897       0      0.376093          79         49
959898       0      0.010333       54335         49
959899       0      0.036321       48447         49

[959900 rows x 4 columns]

In [ ]:
final_results_df = pd.merge(final_results_df, full_balanced_df[['completeness', 'completeness_level']], left_on='test_index', right_index=True, how='left')
final_results_df

y_test  y_pred_proba  test_index  iteration  completeness  \
0            1      0.960844       24203          0     62.247839   
1            1      0.689335       77881          0     80.691643   
2            0      0.027819       50081          0     90.201729   
3            0      0.163814       52555          0     88.472622   
4            1      0.841738       91382          0     80.115274   
...        ...           ...         ...        ...           ...   
959895       1      0.967337       78211         49     85.302594   
959896       0      0.032402       58097         49     89.625360   
959897       0      0.376093          79         49     27.089337   
959898       0      0.010333       54335         49     89.913545   
959899       0      0.036321       48447         49     88.184438   

       completeness_level  
0                     mid  
1                    high  
2                    high  
3                    high  
4                    high  
...                   ...  
959895               high  
959896               high  
959897                low  
959898               high  
959899               high  

[959900 rows x 6 columns]

In [ ]:
final_results_df.to_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new50_XGB_final_results_df.csv', index=False)

In [ ]:
from sklearn import metrics
from sklearn.metrics import f1_score, precision_score, recall_score, roc_auc_score, accuracy_score, balanced_accuracy_score


In [ ]:
def calculate_metrics(y_val, y_pred_proba):
    # Convert predicted probabilities to class labels (0 and 1)
    y_pred_class = (y_pred_proba >= 0.5).astype(int)

    # Calculate the metrics
    metrics = {
        'Metric': ['F1 Score', 'Precision', 'Recall', 'ROC AUC', 'Accuracy', 'Balanced Accuracy'],
        'Value': [f1_score(y_val, y_pred_class),
                   precision_score(y_val, y_pred_class, zero_division=0),
                   recall_score(y_val, y_pred_class),
                   roc_auc_score(y_val, y_pred_proba),
                   accuracy_score(y_val, y_pred_class),
                   balanced_accuracy_score(y_val, y_pred_class)]
    }

    # Create a DataFrame
    df = pd.DataFrame(metrics)

    return df

In [ ]:
def combine_metrics(df_low, df_mid, df_high, calculate_metrics):
    """
    Combines metrics for different completeness levels into a single DataFrame.

    Args:
    - df_low (pd.DataFrame): DataFrame for low completeness level.
    - df_mid (pd.DataFrame): DataFrame for mid completeness level.
    - df_high (pd.DataFrame): DataFrame for high completeness level.
    - calculate_metrics (function): Function to calculate metrics.

    Returns:
    - pd.DataFrame: Combined metrics DataFrame.
    """
    # Calculate metrics for each completeness level
    metrics_low = calculate_metrics(df_low['y_test'], df_low['y_pred_proba'])
    metrics_mid = calculate_metrics(df_mid['y_test'], df_mid['y_pred_proba'])
    metrics_high = calculate_metrics(df_high['y_test'], df_high['y_pred_proba'])


    # Merge metrics DataFrames
    combined_metrics = metrics_low.merge(metrics_mid, on='Metric', suffixes=('_low', '_mid'))
    combined_metrics = combined_metrics.merge(metrics_high, on='Metric', suffixes=('', '_high'))
    combined_metrics = combined_metrics.rename(columns={'Value': 'Value_high'})

    # Clean up combined metrics DataFrame
    combined_metrics = combined_metrics.drop(columns=[col for col in combined_metrics.columns if 'completeness_level' in col])
    combined_metrics = combined_metrics.set_index('Metric')

    return combined_metrics

In [ ]:
for iteration in final_results_df['iteration'].unique():
    # Create sub_df for the current iteration
    sub_df = final_results_df[final_results_df['iteration'] == iteration]

    # Define df_low, df_mid, and df_high based on 'completeness_level'
    df_low = sub_df[sub_df['completeness_level'] == 'low']
    df_mid = sub_df[sub_df['completeness_level'] == 'mid']
    df_high = sub_df[sub_df['completeness_level'] == 'high']

    # Check if all completeness levels exist in the sub_df
    if not (df_low.empty or df_mid.empty or df_high.empty):
        # Run combine_metrics for the current iteration
        combined_metrics_result = combine_metrics(df_low, df_mid, df_high, calculate_metrics)
        print(f"Combined Metrics for Iteration {iteration}:\n{combined_metrics_result}")
    else:
        print(f"Skipping Iteration {iteration}: Not all completeness levels present.")


Combined Metrics for Iteration 0:
                   Value_low  Value_mid  Value_high
Metric                                             
F1 Score            0.704057   0.751585    0.770390
Precision           0.692488   0.738413    0.749506
Recall              0.716019   0.765236    0.792473
ROC AUC             0.767165   0.826257    0.846568
Accuracy            0.705813   0.749740    0.766736
Balanced Accuracy   0.706038   0.749902    0.767050
Combined Metrics for Iteration 1:
                   Value_low  Value_mid  Value_high
Metric                                             
F1 Score            0.699887   0.759441    0.770995
Precision           0.671739   0.744172    0.754954
Recall              0.730496   0.775349    0.787733
ROC AUC             0.760130   0.837643    0.840894
Accuracy            0.689332   0.759477    0.766225
Balanced Accuracy   0.689667   0.759798    0.766243
Combined Metrics for Iteration 2:
                   Value_low  Value_mid  Value_high
Metric        

In [ ]:
# Initialize an empty list to store combined metrics results
combined_metrics_results = []

for iteration in final_results_df['iteration'].unique():
    # Create sub_df for the current iteration
    sub_df = final_results_df[final_results_df['iteration'] == iteration]

    # Define df_low, df_mid, and df_high based on 'completeness_level'
    df_low = sub_df[sub_df['completeness_level'] == 'low']
    df_mid = sub_df[sub_df['completeness_level'] == 'mid']
    df_high = sub_df[sub_df['completeness_level'] == 'high']

    # Check if all completeness levels exist in the sub_df
    if not (df_low.empty or df_mid.empty or df_high.empty):
        # Run combine_metrics for the current iteration
        combined_metrics_result = combine_metrics(df_low, df_mid, df_high, calculate_metrics)
        combined_metrics_result['iteration'] = iteration

        # Append the result to the list
        combined_metrics_results.append(combined_metrics_result)
    else:
        print(f"Skipping Iteration {iteration}: Not all completeness levels present.")



In [ ]:
combined_metrics_result

Value_low  Value_mid  Value_high  iteration
Metric                                                        
F1 Score            0.705618   0.757012    0.767299         49
Precision           0.699332   0.742543    0.751403         49
Recall              0.712018   0.772057    0.783882         49
ROC AUC             0.756414   0.829135    0.839302         49
Accuracy            0.702611   0.753482    0.762801         49
Balanced Accuracy   0.702600   0.753579    0.762848         49

In [ ]:
# Concatenate the list of DataFrames into a single DataFrame
combined_metrics_df = pd.concat(combined_metrics_results, ignore_index=False)

# Set the index to include the iteration number
combined_metrics_df = combined_metrics_df.reset_index().set_index(['iteration', 'Metric'])

In [ ]:
combined_metrics_df

Value_low  Value_mid  Value_high
iteration Metric                                             
0         F1 Score            0.704057   0.751585    0.770390
          Precision           0.692488   0.738413    0.749506
          Recall              0.716019   0.765236    0.792473
          ROC AUC             0.767165   0.826257    0.846568
          Accuracy            0.705813   0.749740    0.766736
...                                ...        ...         ...
49        Precision           0.699332   0.742543    0.751403
          Recall              0.712018   0.772057    0.783882
          ROC AUC             0.756414   0.829135    0.839302
          Accuracy            0.702611   0.753482    0.762801
          Balanced Accuracy   0.702600   0.753579    0.762848

[300 rows x 3 columns]

In [ ]:
combined_metrics_df.to_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new50_XGB_combined_metrics_df.csv')

# Analysis

## Load & concat pred_proba from each model
new_full_results_df.csv

In [ ]:
DT_results = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_DT_final_results_df.csv')
RF_results = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_RF_final_results_df.csv')
LGBM_results = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_LGBM_final_results_df.csv')
XGB_results = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_XGB_final_results_df.csv')


In [ ]:
DT_results.shape

(95990, 6)

In [ ]:
DT_results.head()

y_test  y_pred_proba  test_index  iteration  completeness  \
0       1      0.728723       24203          0     62.247839   
1       1      0.821218       77881          0     80.691643   
2       0      0.213434       50081          0     90.201729   
3       0      0.086096       52555          0     88.472622   
4       1      0.437184       91382          0     80.115274   

  completeness_level  
0                mid  
1               high  
2               high  
3               high  
4               high

In [ ]:
# prompt: for files new_DT_final_results_df.csv, new_RF_final_results_df.csv,  new_LGBM_final_results_df.csv, new_XGB_final_results_df.csv in file_path, save 'y_test', 'y_pred_proba' and rename column to include file name before "_final_results_df" to  a new df results_df, join on test_index and iteration

import pandas as pd

file_paths = {
    'DT': '/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_DT_final_results_df.csv',
    'RF': '/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_RF_final_results_df.csv',
    'LGBM': '/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_LGBM_final_results_df.csv',
    'XGB': '/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_XGB_final_results_df.csv'
}

results_df = pd.DataFrame()

for model_name, file_path in file_paths.items():
    temp_df = pd.read_csv(file_path)
    temp_df = temp_df[['y_test', 'y_pred_proba', 'test_index', 'iteration']]
    temp_df = temp_df.rename(columns={'y_test': f'{model_name}_y_test', 'y_pred_proba': f'{model_name}_y_pred_proba'})

    if results_df.empty:
        results_df = temp_df
    else:
        results_df = pd.merge(results_df, temp_df, on=['test_index', 'iteration'], how='left')

results_df


DT_y_test  DT_y_pred_proba  test_index  iteration  RF_y_test  \
0              1         0.728723       24203          0          1   
1              1         0.821218       77881          0          1   
2              0         0.213434       50081          0          0   
3              0         0.086096       52555          0          0   
4              1         0.437184       91382          0          1   
...          ...              ...         ...        ...        ...   
95985          0         0.731312       55755          4          0   
95986          1         0.720000       36979          4          1   
95987          1         0.499047       77585          4          1   
95988          0         0.169804       10180          4          0   
95989          1         0.731312       22071          4          1   

       RF_y_pred_proba  LGBM_y_test  LGBM_y_pred_proba  XGB_y_test  \
0             0.749422            1           0.863152           1   
1             0.645641            1           0.804602           1   
2             0.172363            0           0.046961           0   
3             0.172207            0           0.116721           0   
4             0.585506            1           0.688801           1   
...                ...          ...                ...         ...   
95985         0.648674            0           0.620370           0   
95986         0.568987            1           0.783444           1   
95987         0.541091            1           0.669812           1   
95988         0.277820            0           0.292263           0   
95989         0.629120            1           0.809786           1   

       XGB_y_pred_proba  
0              0.960844  
1              0.689335  
2              0.027819  
3              0.163814  
4              0.841738  
...                 ...  
95985          0.632732  
95986          0.842788  
95987          0.749511  
95988          0.340391  
95989          0.884908  

[95990 rows x 10 columns]

In [ ]:
inconsistent_rows = results_df[
    results_df['DT_y_test'] != results_df['RF_y_test']
    | (results_df['DT_y_test'] != results_df['LGBM_y_test'])
    | (results_df['DT_y_test'] != results_df['XGB_y_test'])
    | (results_df['RF_y_test'] != results_df['LGBM_y_test'])
    | (results_df['RF_y_test'] != results_df['XGB_y_test'])
    | (results_df['LGBM_y_test'] != results_df['XGB_y_test'])
]

print("Number of inconsistent rows:", len(inconsistent_rows))
inconsistent_rows.head()


Number of inconsistent rows: 0


Empty DataFrame
Columns: [DT_y_test, DT_y_pred_proba, test_index, iteration, RF_y_test, RF_y_pred_proba, LGBM_y_test, LGBM_y_pred_proba, XGB_y_test, XGB_y_pred_proba]
Index: []

In [ ]:
DT_results.shape
DT_results.head()

y_test  y_pred_proba  test_index  iteration  completeness  \
0       1      0.728723       24203          0     62.247839   
1       1      0.821218       77881          0     80.691643   
2       0      0.213434       50081          0     90.201729   
3       0      0.086096       52555          0     88.472622   
4       1      0.437184       91382          0     80.115274   

  completeness_level  
0                mid  
1               high  
2               high  
3               high  
4               high

In [ ]:
results_df.shape
results_df.head()

DT_y_test  DT_y_pred_proba  test_index  iteration  RF_y_test  \
0          1         0.728723       24203          0          1   
1          1         0.821218       77881          0          1   
2          0         0.213434       50081          0          0   
3          0         0.086096       52555          0          0   
4          1         0.437184       91382          0          1   

   RF_y_pred_proba  LGBM_y_test  LGBM_y_pred_proba  XGB_y_test  \
0         0.749422            1           0.863152           1   
1         0.645641            1           0.804602           1   
2         0.172363            0           0.046961           0   
3         0.172207            0           0.116721           0   
4         0.585506            1           0.688801           1   

   XGB_y_pred_proba  
0          0.960844  
1          0.689335  
2          0.027819  
3          0.163814  
4          0.841738

In [ ]:
# Rename 'DT_y_test' to 'y_test'
results_df = results_df.rename(columns={'DT_y_test': 'y_test'})

# Drop columns
results_df = results_df.drop(['RF_y_test', 'LGBM_y_test', 'XGB_y_test'], axis=1)

results_df.head()

y_test  DT_y_pred_proba  test_index  iteration  RF_y_pred_proba  \
0       1         0.728723       24203          0         0.749422   
1       1         0.821218       77881          0         0.645641   
2       0         0.213434       50081          0         0.172363   
3       0         0.086096       52555          0         0.172207   
4       1         0.437184       91382          0         0.585506   

   LGBM_y_pred_proba  XGB_y_pred_proba  
0           0.863152          0.960844  
1           0.804602          0.689335  
2           0.046961          0.027819  
3           0.116721          0.163814  
4           0.688801          0.841738

In [ ]:
# prompt: add 'completeness_level' from DT_results to results_df, merge on text_index and iteration

# Merge 'completeness_level' from DT_results to results_df
results_df = pd.merge(results_df, DT_results[['test_index', 'iteration', 'completeness_level']], on=['test_index', 'iteration'], how='left')

results_df.shape
results_df.head()


y_test  DT_y_pred_proba  test_index  iteration  RF_y_pred_proba  \
0       1         0.728723       24203          0         0.749422   
1       1         0.821218       77881          0         0.645641   
2       0         0.213434       50081          0         0.172363   
3       0         0.086096       52555          0         0.172207   
4       1         0.437184       91382          0         0.585506   

   LGBM_y_pred_proba  XGB_y_pred_proba completeness_level  
0           0.863152          0.960844                mid  
1           0.804602          0.689335               high  
2           0.046961          0.027819               high  
3           0.116721          0.163814               high  
4           0.688801          0.841738               high

In [ ]:
results_df.shape

(95990, 8)

In [ ]:
# prompt: for each iteration in results_df['iteration'], set_index(test_index) and merge with balanced_df, left_index=True, right_index=True, how='left'
full_results_df = pd.DataFrame()
for iteration in results_df['iteration'].unique():
    temp_df = results_df[results_df['iteration'] == iteration].set_index('test_index')
    temp_df = pd.merge(temp_df, balanced_df['case_id'], left_index=True, right_index=True, how='left')

    full_results_df = pd.concat([full_results_df, temp_df], axis=0)

In [ ]:
full_results_df

y_test  DT_y_pred_proba  iteration  RF_y_pred_proba  \
test_index                                                        
24203            1         0.728723          0         0.749422   
77881            1         0.821218          0         0.645641   
50081            0         0.213434          0         0.172363   
52555            0         0.086096          0         0.172207   
91382            1         0.437184          0         0.585506   
...            ...              ...        ...              ...   
55755            0         0.731312          4         0.648674   
36979            1         0.720000          4         0.568987   
77585            1         0.499047          4         0.541091   
10180            0         0.169804          4         0.277820   
22071            1         0.731312          4         0.629120   

            LGBM_y_pred_proba  XGB_y_pred_proba completeness_level  case_id  
test_index                                                                   
24203                0.863152          0.960844                mid   642035  
77881                0.804602          0.689335               high  1539041  
50081                0.046961          0.027819               high  1817081  
52555                0.116721          0.163814               high  1435206  
91382                0.688801          0.841738               high  2560708  
...                       ...               ...                ...      ...  
55755                0.620370          0.632732               high  1850819  
36979                0.783444          0.842788                mid  2545514  
77585                0.669812          0.749511               high  1530306  
10180                0.292263          0.340391                mid   993647  
22071                0.809786          0.884908                mid    44034  

[95990 rows x 8 columns]

In [ ]:
len(full_results_df['case_id'].unique())

64410

In [ ]:
full_results_df.to_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_full_results_df.csv', index=False)

## Load and concat combined_metrics from each model
new_all_metrics.csv


In [ ]:
DT_metric = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_DT_combined_metrics_df.csv')
RF_metric = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_RF_combined_metrics_df.csv')
LGBM_metric = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_LGBM_combined_metrics_df.csv')
XGB_metric = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_XGB_combined_metrics_df.csv')


In [ ]:
DT_metric

iteration             Metric  Value_low  Value_mid  Value_high
0           0           F1 Score   0.635707   0.702047    0.712565
1           0          Precision   0.552962   0.662493    0.685278
2           0             Recall   0.747573   0.746623    0.742115
3           0            ROC AUC   0.591174   0.746676    0.764722
4           0           Accuracy   0.581257   0.686470    0.704354
5           0  Balanced Accuracy   0.584923   0.687097    0.704816
6           1           F1 Score   0.637188   0.693072    0.691800
7           1          Precision   0.612200   0.677691    0.688086
8           1             Recall   0.664303   0.709168    0.695555
9           1            ROC AUC   0.640860   0.752011    0.762515
10          1           Accuracy   0.624853   0.692433    0.690394
11          1  Balanced Accuracy   0.625175   0.692772    0.690399
12          2           F1 Score   0.664200   0.711316    0.711993
13          2          Precision   0.547256   0.667346    0.680474
14          2             Recall   0.844706   0.761489    0.746574
15          2            ROC AUC   0.620868   0.756043    0.763663
16          2           Accuracy   0.577907   0.687684    0.698110
17          2  Balanced Accuracy   0.580974   0.686894    0.698127
18          3           F1 Score   0.667904   0.704511    0.699933
19          3          Precision   0.544629   0.667895    0.682251
20          3             Recall   0.863309   0.745374    0.718556
21          3            ROC AUC   0.593828   0.746843    0.759235
22          3           Accuracy   0.584204   0.686312    0.691255
23          3  Balanced Accuracy   0.592691   0.686111    0.691194
24          4           F1 Score   0.652542   0.689834    0.685634
25          4          Precision   0.583333   0.699104    0.697072
26          4             Recall   0.740385   0.680806    0.674566
27          4            ROC AUC   0.645101   0.755801    0.761251
28          4           Accuracy   0.612751   0.693893    0.692216
29          4  Balanced Accuracy   0.614972   0.693893    0.692130

In [ ]:
DT_metric.shape

(30, 5)

In [ ]:
# prompt: create a new dataframe to concat all metric tables DT_metric, RF_metric, LGBM_metric and XGB_metric and add a new column for model name from "_metric"

import pandas as pd

# Load the metric dataframes
DT_metric = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_DT_combined_metrics_df.csv')
RF_metric = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_RF_combined_metrics_df.csv')
LGBM_metric = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_LGBM_combined_metrics_df.csv')
XGB_metric = pd.read_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_XGB_combined_metrics_df.csv')

# Add a column for the model name
DT_metric['Model'] = 'DT'
RF_metric['Model'] = 'RF'
LGBM_metric['Model'] = 'LGBM'
XGB_metric['Model'] = 'XGB'

# Concatenate the dataframes
all_metrics = pd.concat([DT_metric, RF_metric, LGBM_metric, XGB_metric], ignore_index=True)

# Display the combined dataframe
all_metrics


iteration             Metric  Value_low  Value_mid  Value_high Model
0            0           F1 Score   0.635707   0.702047    0.712565    DT
1            0          Precision   0.552962   0.662493    0.685278    DT
2            0             Recall   0.747573   0.746623    0.742115    DT
3            0            ROC AUC   0.591174   0.746676    0.764722    DT
4            0           Accuracy   0.581257   0.686470    0.704354    DT
..         ...                ...        ...        ...         ...   ...
115          4          Precision   0.690867   0.743297    0.746833   XGB
116          4             Recall   0.709135   0.783995    0.779667   XGB
117          4            ROC AUC   0.769365   0.836272    0.837324   XGB
118          4           Accuracy   0.701299   0.756619    0.758865   XGB
119          4  Balanced Accuracy   0.701435   0.756619    0.758966   XGB

[120 rows x 6 columns]

In [ ]:
all_metrics.to_csv('/content/drive/My Drive/Colab Notebooks/CreditFairness/HomeCreditStability/Results/new_all_metrics.csv', index=False)

## Normality Test


In [ ]:
low_data = all_metrics['Value_low']
mid_data = all_metrics['Value_mid']
high_data = all_metrics['Value_high']

In [ ]:
import numpy as np
from scipy import stats
import matplotlib.pyplot as plt

In [ ]:
# Shapiro-Wilk Test
stat, p = stats.shapiro(low_data)
print(f"Shapiro-Wilk Test: stat={stat:.4f}, p={p:.4f}")

stat, p = stats.shapiro(mid_data)
print(f"Shapiro-Wilk Test: stat={stat:.4f}, p={p:.4f}")

stat, p = stats.shapiro(high_data)
print(f"Shapiro-Wilk Test: stat={stat:.4f}, p={p:.4f}")

Shapiro-Wilk Test: stat=0.9643, p=0.0029
Shapiro-Wilk Test: stat=0.9500, p=0.0002
Shapiro-Wilk Test: stat=0.9604, p=0.0014


In [ ]:
from scipy import stats
l_stat = stats.kstest(low_data, 'norm')
l_stat


KstestResult(statistic=0.7069957675542693, pvalue=6.911815998412476e-61, statistic_location=0.5446293494704992, statistic_sign=-1)

In [ ]:
m_stat = stats.kstest(mid_data, 'norm')
m_stat

KstestResult(statistic=0.7461724492978139, pvalue=1.9293761083121682e-69, statistic_location=0.6624933404368674, statistic_sign=-1)

In [ ]:
h_stat = stats.kstest(high_data, 'norm')
h_stat

KstestResult(statistic=0.7500243488496579, pvalue=2.433028682511459e-70, statistic_location=0.6745663747209343, statistic_sign=-1)